In [ ]:
from datasets import load_dataset, DatasetDict, concatenate_datasets

columns = set(['premise', 'hypothesis', 'subset', 'label_name'])

# SNLI


In [ ]:
snli = load_dataset('snli')
snli = DatasetDict({'train': snli['train'], 'test': snli['validation']})
snli

In [ ]:
mapping = {0: 'entailment', 1: 'non-entailment', 2: 'non-entailment'}

def label_name(sample):
    sample['label_name'] = mapping[sample['label']]
    sample['subset'] = 'snli'
    return sample

snli = snli.filter(lambda x: x['label'] != -1, batched=False)
snli = snli.map(label_name, batched=False, remove_columns=list(set(snli['train'].column_names) - columns))
snli

# MNLI

In [ ]:
mnli = load_dataset('multi_nli')
mnli = DatasetDict({'train': mnli['train'], 'test': mnli['validation_matched']})
mnli

In [ ]:
mapping = {0: 'entailment', 1: 'non-entailment', 2: 'non-entailment'}

def label_name(sample):
    sample['label_name'] = mapping[sample['label']]
    sample['subset'] = 'mnli'
    return sample

mnli = mnli.map(label_name, batched=False, remove_columns=list(set(mnli['train'].column_names) - columns))
mnli

# FEVER

In [ ]:
fever = load_dataset('pietrolesci/nli_fever')
fever = DatasetDict({'train': fever['train'], 'test': fever['dev']})
fever

In [ ]:
mapping = {'SUPPORTS': 'entailment', 'REFUTES': 'non-entailment', 'NOT ENOUGH INFO': 'non-entailment'}

def label_name(sample):
    sample['label_name'] = mapping[sample['fever_gold_label']]
    sample['subset'] = 'fever'
    return sample

fever = fever.map(label_name, batched=False, remove_columns=list(set(fever['train'].column_names) - columns))
fever

# SciTail

In [ ]:
scitail = load_dataset('scitail', 'snli_format')
scitail = DatasetDict({'train': scitail['train'], 'test': scitail['validation']})
scitail

In [ ]:
mapping = {'entailment': 'entailment', 'neutral': 'non-entailment'}

def label_name(sample):
    sample['label_name'] = mapping[sample['gold_label']]
    sample['premise'] = sample['sentence1']
    sample['hypothesis'] = sample['sentence2']
    sample['subset'] = 'scitail'
    return sample

scitail = scitail.map(label_name, batched=False, remove_columns=list(set(scitail['train'].column_names) - columns))
scitail

# PAWS

In [ ]:
paws = load_dataset('paws', 'labeled_final')
paws = DatasetDict({'train': paws['train'], 'test': paws['validation']})
paws

In [ ]:
mapping = {1: 'entailment', 0: 'non-entailment'}

def label_name(sample):
    sample['label_name'] = mapping[sample['label']]
    sample['premise'] = sample['sentence1']
    sample['hypothesis'] = sample['sentence2']
    sample['subset'] = 'paws'
    return sample

paws = paws.map(label_name, batched=False, remove_columns=list(set(paws['train'].column_names) - columns))
paws

# VitaminC

In [ ]:
vitaminc = load_dataset('tals/vitaminc')
vitaminc = DatasetDict({'train': vitaminc['train'], 'test': vitaminc['validation']})
vitaminc

In [ ]:
mapping = {'SUPPORTS': 'entailment', 'REFUTES': 'non-entailment', 'NOT ENOUGH INFO': 'non-entailment'}

def label_name(sample):
    sample['label_name'] = mapping[sample['label']]
    sample['premise'] = sample['evidence']
    sample['hypothesis'] = sample['claim']
    sample['subset'] = 'vitaminc'
    return sample

vitaminc = vitaminc.map(label_name, batched=False, remove_columns=list(set(vitaminc['train'].column_names) - columns))
vitaminc

# NLI Mixture

In [ ]:
nli_train = concatenate_datasets([snli['train'], mnli['train'], fever['train'], scitail['train'], paws['train'], vitaminc['train']])
nli_test = concatenate_datasets([snli['test'], mnli['test'], fever['test'], scitail['test'], paws['test'], vitaminc['test']])

nli_dataset = DatasetDict({'train': nli_train, 'test': nli_test})
nli_dataset

In [ ]:
nli_dataset.push_to_hub('AntoineBlanot/nli_mixture')